# Imports

In [1]:
import pandas as pd
#Dict approach
import glob
import os
import sys
from pathlib import Path
#from typing import Any, Optional
import numpy as np
import pandas as pd
import torch
from torch.utils.data import Dataset, DataLoader
import h5py
from sklearn.metrics import r2_score

# Load genome loaders

In [2]:
#Load genome loader for salk cluster
sys.path.append('/iblm/netapp/home/jjaureguy/genome_loader/genome-loader')

In [3]:
#Load genome loader for runAI clusterMJ
sys.path.append('/home/jovyan/home/jjaureguy/genome_loader/genome-loader')

In [4]:

import genome_loader.write_h5
import genome_loader.encode_data
import genome_loader.get_data
import genome_loader.get_encoded
import genome_loader.load_data
import genome_loader.load_h5

from genome_loader.write_h5 import write_encoded_genome
 

# Load in dataframes for Train/valid/test on runAI cluster


In [5]:
#OHE for AGCT
one_hot_enc_genome = h5py.File('/home/jovyan/data4/jjaureguy/out_dir/genome_onehot.h5','r')
frag_tn5_train_df = pd.read_csv('/home/jovyan/data4/jjaureguy/jupyter/data_frames/runai_df/train_frag_tn5_h5_df_runai.txt',sep='\t')
frag_tn5_valid_df = pd.read_csv('/home/jovyan/data4/jjaureguy/jupyter/data_frames/runai_df/valid_frag_tn5_h5_df_runai.txt',sep='\t')
frag_tn5_test_df = pd.read_csv('/home/jovyan/data4/jjaureguy/jupyter/data_frames/runai_df/test_frag_tn5_h5_df_runai.txt',sep='\t')



train_bed_file_df = pd.read_csv('/home/jovyan/data4/UCSC_browser_lab_data/jjaureguy/ml_proj/bed_files/pos_training_regression/fikt_3_train_df_filtered_500_final_pos.txt', names=['chrom','start','end'], sep='\t')
valid_df = pd.read_csv('/home/jovyan/data4/UCSC_browser_lab_data/jjaureguy/ml_proj/bed_files/pos_training_regression/fikt_3_valid_df_filtered_500_final_pos.txt', sep='\t', names = ['chrom', 'start','end'])
test_bed_file_df = pd.read_csv('/home/jovyan/data4/UCSC_browser_lab_data/jjaureguy/ml_proj/bed_files/pos_training_regression/fikt_3_test_df_filtered_500_final_pos.txt', names=['chrom','start','end'], sep='\t')


In [6]:
fikt_3 = frag_tn5_train_df[frag_tn5_train_df['patient_id']=='HPSI0114i-fikt_3']

In [7]:
fikt_3 = fikt_3.reset_index(drop=True)

In [8]:
fikt_3

patient_id                                  diff_frag_h5_path  \
0  HPSI0114i-fikt_3  /home/jovyan/data3/jjaureguy/PRJEB18997/10_gen...   

                         int_gamma_diff_frag_h5_path  \
0  /home/jovyan/data3/jjaureguy/PRJEB18997/10_gen...   

                    salm_int_gamma_diff_frag_h5_path  \
0  /home/jovyan/data3/jjaureguy/PRJEB18997/10_gen...   

                              salm_diff_frag_h5_path  
0  /home/jovyan/data3/jjaureguy/PRJEB18997/10_gen...

# Dataframe

# Dataset Custom Class

In [9]:
# Imports
from enum import Enum
from pathlib import Path
from typing import Any, Optional
from torch import nn
import pytorch_lightning as pl
import h5py
from tqdm.notebook import tqdm
#from .transforms import KmerShuffle

# DataSet Class

In [14]:
import h5py 
import random
from collections import defaultdict

class Dataset_class(Dataset):
    """Dataset_class Dataset.

    Parameters
    ----------
    one_hot_enc_genome object: pass the H5py file object. One-hot encoded genome `.h5` file. e.g. from genome-loader.
    unified_bed_file_df : pass the df object. DF of bed file containing unified peak set of (1st 5 patients). Chrom, start, end.  
    frag_tn5_h5_df: pass the df object. DF containing H5py paths for Tn5 read counts. Patient ID, treatment type, H5py path column containg Tn5 read counts
    """
    # class constructor(initialize ohe, bed file, frag df file)
    def __init__(self, one_hot_enc_genome, unified_bed_file_df, frag_tn5_h5_df,bin_size, dtype = torch.float32):
        super().__init__()
        self.bin_size = bin_size
        self.one_hot_enc_genome = one_hot_enc_genome
        self.unified_bed_file_df = unified_bed_file_df
        self.frag_tn5_h5_df_1 = frag_tn5_h5_df
        self.frag_tn5_h5_df_2 = frag_tn5_h5_df
        self.frag_tn5_h5_df_3 = frag_tn5_h5_df
        self.frag_tn5_h5_df_4 = frag_tn5_h5_df
        self.dtype = dtype
        # Empty dictionary for h5 file paths
        self.h5_files = {}
        #self.d = defaultdict(list)

    # Takes in h5 path from Tn5 from frag_tn5_h5_df column containing h5 paths of Tn5 counts
    def get_h5(self, h5_path):
        # checks if h5 path is already in dictionary of h5py file paths
        if h5_path in self.h5_files:
            # returns them if there already there
            return self.h5_files[h5_path]
        else:
            # Sets the path as a key, and the value as the read file
            self.h5_files[h5_path] = h5py.File(h5_path, "r")
            
    """Function: selects random midpoint from X features(one hot encoded ref genome peak range)
          1) pick random point in range_num(list) and set to variable
    """
    def get_mid_point(self, start, end):
        #np.random.seed(0)
        mid_point = int((start+end)/2)
        #mid_point = np.random.choice(mid_point, 1, replace=True)
        #print('mid pt selection random', (mid_point))
        #mid_point = mid_point.item()
        return mid_point
    
    
    """Function: selects 1024 bp window of X features(one hot encoded ref genome peak range)
          1) utilizes mid point from get_mid_point
          2) creates a 1024 window size around midpoint
    """
    def get_x_window(self,mid_point, d):
        bounds = (mid_point-512, mid_point + 512)
        d['1024_bp_start_end'] = bounds
        bounds = range(mid_point-512, mid_point + 512)
        mid_point = list(bounds)
        return mid_point
    
    """Function: selects 256 bp window of Y features(Tn5 frag counts from h5py file)
          1) utilize sames mid point from get_mid_point
          2) creates a 256 window size around midpoint
    """
    def get_y_window(self,mid_point):
        # same thing but without check since 256 bp window is within the 1024bp window
        mid_point = list(range(mid_point-256, mid_point + 256))
        return mid_point
    
    
    """Function: Takes Total Tn5 counts per chromosome and counts per window
          Calculates the Atac normalization of Tn5 cut sites counts
          Tn5_counts_window = Tn5 bp window that corresponds to the OHE region of the genome (X feature)
          C = sum of the Counts per window(summed bp region)
          T = total_tn5_counts_per_chrom for h5py file
    """
    def normalize_atac_reads(self, Tn5_counts_window, T,d):
        self.Tn5_counts_window = Tn5_counts_window
        self.T = T
        counts = []
        
        for i in range(len(Tn5_counts_window)):
            C = np.sum(Tn5_counts_window[i])
            length = len(Tn5_counts_window[i])
            norm = (C*10**9/(T*(length)))
            counts.append(norm)
        return (counts, C)
    
    """Function: Window size and bins by bin_size
          window = 256 bp window
          bin_size = 1,2,4,6,8,16,32,64,128,256
    """
    def bin_window(self, window,  bin_size):
        self.window = window
        self.bin_size = bin_size 
        length_window = len(window)
        bins = []
        for i in range(0, length_window, bin_size):
            bins.append((window[i:i+bin_size]))
        return bins
    """Function: returns length of dataset of X*Y
    """
    def __len__(self):
        return (len(self.unified_bed_file_df)*len(self.frag_tn5_h5_df_1))
    
    """Function: returns X,Y from OHE genome h5py file and Tn5 frag counts h5py file
    
    """
    def __getitem__(self,index: int):
        
        #create sequence of strings for keys
        dict_keys = ('Chrom','1024_bp_start_end','Patient_ID','y','C_1', 'Peak_coords', 'T', 'C_1_norm')
        # 'C_2', 'C_3', 'C_4',
        
        #create the dictionary, `my_dictionary`, using the fromkeys() method
        d = defaultdict(list).fromkeys(dict_keys)
        bam_file_index = (index % len(self.frag_tn5_h5_df_1))
        peak_index = (index // len(self.frag_tn5_h5_df_1))
        # object that contains chrom, start, end
        coords = self.unified_bed_file_df.iloc[peak_index]
        # Picks midpoint from coors(bed file peak region)
        d['Peak_coords'] = coords.start,coords.end
        # Add chrom coords to dictionary 
        d['Chrom'] = coords.chrom
        window = (self.get_mid_point(coords.start,coords.end))
        # create X from OHE genome at the bed file peak region with 1024 bp window size
        # Window for x and dictionary
        temp = self.get_x_window(window, d)
        x =  self.one_hot_enc_genome[coords.chrom]['onehot'][temp]
        # Add start,end window coords to dictionary
        #self.d['1024_bp_start_end'] = temp[::len(temp)-1]
        

        # To tensor when running on runAI
        x = torch.as_tensor(x,  dtype=self.dtype)
        # reads in h5py path from Col 1(treatment type) in df of h5py Tn5 insertion cutsite h5 paths
        self.get_h5(self.frag_tn5_h5_df_1.iloc[ bam_file_index, self.frag_tn5_h5_df_1.columns.get_loc('diff_frag_h5_path')])
        
        # Add patient id to dictionary
        d['Patient_ID'] = (self.frag_tn5_h5_df_1.iloc[ bam_file_index, self.frag_tn5_h5_df_1.columns.get_loc('patient_id')])
        #Gets the h5py path at the bam index from dictionary of h5py paths
        h5_tn5_read_count_diff = self.h5_files.get(self.frag_tn5_h5_df_1.iloc[ bam_file_index, self.frag_tn5_h5_df_1.columns.get_loc('diff_frag_h5_path')])
        
        
        # Total total_tn5_counts for all chroms
        T_1 = h5_tn5_read_count_diff.attrs["total_sum"]
        d['T'] = T_1
        #Adds T_1 Tn5 counts value to dictionary
        #self.d['T1_diff_counts'] = T_1
        
        # Sets y1 to 256 bp window from h5py Tn5 insertion cutsites corresponding to OHE genome window
        y_1  = (h5_tn5_read_count_diff[coords.chrom]['depth'][self.get_y_window(window)])
        # Bin window based off bin_size
        y_1 = self.bin_window(window=y_1,bin_size=self.bin_size)
        #Normalize each bin windowy_1 = self.bin_window(window=y_1,bin_size=self.bin_size)
        norm_1 = self.normalize_atac_reads(y_1, T_1, d)
        #self.d['Norm_1'] = norm_1

#         # reads in h5py path from Col 2(treatment type) in df of h5py Tn5 insertion cutsite h5 paths
#         self.get_h5(self.frag_tn5_h5_df_2.iloc[ bam_file_index, self.frag_tn5_h5_df_2.columns.get_loc('int_gamma_diff_frag_h5_path')])
        
#         #Gets the h5py path at the bam index from dictionary of h5py paths
#         h5_tn5_read_count_int_gamma = self.h5_files.get(self.frag_tn5_h5_df_2.iloc[ bam_file_index, self.frag_tn5_h5_df_2.columns.get_loc('int_gamma_diff_frag_h5_path')])
#         # Total total_tn5_counts for all chroms
#         T_2 = h5_tn5_read_count_int_gamma.attrs["total_sum"]
#         #Adds T_2 Tn5 counts value to dictionary
#         #self.d['T2_int_gamma_diff_counts'] = T_2
#         # Sets y2 to 256 bp window from h5py Tn5 insertion cutsites corresponding to OHE genome window
#         y_2 = (h5_tn5_read_count_int_gamma[coords.chrom]['depth'][self.get_y_window(window)])
#         # Bin window based off bin_size
#         y_2 = self.bin_window(window=y_2,bin_size=self.bin_size)
#         #Normalize bins in window
#         norm_2 = self.normalize_atac_reads(y_2, T_2, d)
#         #self.d['Norm_2'] = norm_2
#         # reads in h5py path from Col 3(treatment type) in df of h5py Tn5 insertion cutsite h5 paths
#         self.get_h5(self.frag_tn5_h5_df_3.iloc[ bam_file_index, self.frag_tn5_h5_df_3.columns.get_loc('salm_int_gamma_diff_frag_h5_path')])
#         #Gets the h5py path at the bam index from dictionary of h5py paths
#         h5_tn5_read_count_salm_int_gamma = self.h5_files.get(self.frag_tn5_h5_df_3.iloc[ bam_file_index, self.frag_tn5_h5_df_3.columns.get_loc('salm_int_gamma_diff_frag_h5_path')])
#         # Total total_tn5_counts for all chroms
#         T_3 = h5_tn5_read_count_salm_int_gamma.attrs["total_sum"]
#         #Adds T_3 Tn5 counts value to dictionary
#         #self.d['T3_salm_int_gamma_counts'] = T_3
        
        
#         # Sets y3 to 256 bp window from h5py Tn5 insertion cutsites corresponding to OHE genome window
#         y_3 = (h5_tn5_read_count_salm_int_gamma[coords.chrom]['depth'][self.get_y_window(window)])
#         # Bin window based off bin_size
#         y_3 = self.bin_window(window=y_3,bin_size=self.bin_size)
#         #Normalize bins in window
#         norm_3 = self.normalize_atac_reads(y_3, T_3, d)
#         #self.d['Norm_3'] = norm_3

#         # reads in h5py path from Col 4(treatment type) in df of h5py Tn5 insertion cutsite h5 paths
#         self.get_h5(self.frag_tn5_h5_df_4.iloc[ bam_file_index, self.frag_tn5_h5_df_4.columns.get_loc('salm_diff_frag_h5_path')])
#         #Gets the h5py path at the bam index from dictionary of h5py paths
#         h5_tn5_read_count_salm_diff = self.h5_files.get(self.frag_tn5_h5_df_4.iloc[ bam_file_index, self.frag_tn5_h5_df_4.columns.get_loc('salm_diff_frag_h5_path')])
#         T_4 = h5_tn5_read_count_salm_diff.attrs["total_sum"]
        
#         #Adds T_4 Tn5 counts value to dictionary
#         #self.d['T4_salm_counts'] = T_4
        
#         # Sets y4 to 256 bp window from h5py Tn5 insertion cutsites corresponding to OHE genome window
#         y_4 = (h5_tn5_read_count_salm_diff[coords.chrom]['depth'][self.get_y_window(window)])
#         # Bin window based off bin_size
#         y_4 = self.bin_window(window=y_4,bin_size=self.bin_size)
#         #Normalize bins in window
#         norm_4 = self.normalize_atac_reads(y_4, T_4, d)
#         #self.d['Norm_4'] = norm_4
#         # concatenate 4 windows(based off bin_size) to create concatenated bp window of four treatments corresponding to OHE genome 1024 bp window
#         y = np.concatenate((norm_1[0],norm_2[0],norm_3[0],norm_4[0]))
        #c = np.stack((norm_1[1],norm_2[1],norm_3[1],norm_4[1]))
        y = norm_1[0]
        C_1 = norm_1[1]
        C_1_norm = norm_1[0]
#         C_2 = norm_2[1]
#         C_3 = norm_3[1]
#         C_4 = norm_4[1]
        d['y'] = y 
        d['C_1'] = C_1
        d['C_1_norm'] = C_1_norm
#         d['C_2'] = C_2
#         d['C_3'] = C_3
#         d['C_4'] = C_4
        # To tensor when running on runAI
        y = torch.as_tensor(y, dtype=self.dtype)

        #Returns tuple of X,y ((1024,4),(bin size related)) size
        return x, y


In [15]:
# Experimental plots

In [16]:
DS_valid = Dataset_class(one_hot_enc_genome, valid_df, fikt_3,bin_size = 512)

In [17]:
DS_valid.__getitem__(0)

(tensor([[0., 1., 0., 0.],
         [0., 0., 0., 1.],
         [0., 0., 1., 0.],
         ...,
         [0., 0., 0., 1.],
         [0., 1., 0., 0.],
         [0., 1., 0., 0.]]),
 tensor([5.9415]))

# Imports for pytorch lightning and wandb

In [19]:
import wandb
from pytorch_lightning.loggers import WandbLogger
# Pytorch modules
import torch
from torch.nn import functional as F
from torch import nn
from torch.optim import Adam
from torch.utils.data import DataLoader, random_split
from torch.utils.data import Dataset, DataLoader
from pytorch_lightning import LightningDataModule, LightningModule, Trainer
import pytorch_lightning as pl



# Definining our model(Naive CC)

In [20]:
class LitNN(LightningModule):
    def __init__(self,seq_len=1024, channels= 4,num_classes=1, n_layer_1=128, n_layer_2=64, n_layer_3=32 ,lr=1e-3):
        """
        init convolution and activation layers
        Args:
        x: (Nx1x2004)
        class: 

        """
        super().__init__() 
        
        self.conv1 = torch.nn.Conv1d(channels, n_layer_1, kernel_size=3)
        self.batch1 = nn.BatchNorm1d(n_layer_1)
        self.relu = torch.nn.ReLU()
        self.conv2 = torch.nn.Conv1d(n_layer_1, n_layer_2, kernel_size=3)
        self.batch2 = nn.BatchNorm1d(n_layer_2)
        self.conv3 = torch.nn.Conv1d(n_layer_2, n_layer_3, kernel_size=3)
        self.batch3 = nn.BatchNorm1d( n_layer_3)
        self.pool = torch.nn.MaxPool1d(4)
        self.fc1 = torch.nn.Linear(480, num_classes)
        
        # optimizer parameters
        self.lr = lr

        # metrics
        self.R2score_normal = torchmetrics.R2Score(num_outputs = 1)
        self.R2score_flipped = torchmetrics.R2Score(num_outputs = 1)
        self.MSE = torchmetrics.MeanSquaredError()
        self.pearson_cor = torchmetrics.PearsonCorrCoef()

        # optional - save hyper-parameters to self.hparams
        # they will also be automatically logged as config parameters in W&B
        self.save_hyperparameters()

    def forward(self, x):
        """
        forward function describes how input tensor is transformed to output tensor
        Args:
            
        """
        
        batch_size,  seq_len, channels = x.size()
        # Changes the order to batch_size, channels, seq_len 
        x = x.permute(0,2,1)
        x = self.conv1(x)
        x = self.batch1(x)
        x = self.relu(x)
        x = self.pool(x)
        x = self.conv2(x)
        x = self.batch2(x)
        x = self.relu(x)
        x = self.pool(x)
        x = self.conv3(x)
        x = self.batch3(x)
        x = self.relu(x)
        x = self.pool(x)
        #Flatten layer for fully connected layer
        x = torch.flatten(x, 1)
        x = self.fc1(x)
        return x
    

    def training_step(self, batch, batch_idx):
        '''needs to return a loss from a single batch'''
        x, y = batch
        logits = self(x)
        loss = F.mse_loss(logits, y)

        # Log training loss
        self.log('train_loss', loss)

        # Log metrics
        self.log('train_flipped_R2', self.R2score_flipped(y,logits))
        self.log('train_normal_R2', self.R2score_normal(logits,y))
        self.log('train_mse', self.MSE(logits, y))
        self.log('train_pearson_corr', self.pearson_cor(logits, y))
        return loss

    def validation_step(self, batch, batch_idx):
        '''used for logging metrics'''
        x, y = batch
        logits = self(x)
        loss = F.mse_loss(logits, y)
        
        # Log validation loss (will be automatically averaged over an epoch)
        self.log('valid_loss', loss)

        # Log metrics
        self.log('valid_R2_flipped_R2', self.R2score_flipped(y,logits))
        self.log('valid_R2_normal_R2', self.R2score_normal(logits,y))
        self.log('valid_rmse', self.MSE(logits, y))
        self.log('valid_peasron_corr', self.pearson_cor(logits, y))
        return loss

    def test_step(self, batch, batch_idx):
        '''used for logging metrics'''
        x, y = batch
        logits = self(x)
        loss = F.mse_loss(logits, y)

        # Log test loss
        self.log('test_loss', loss)


        # Log metrics
        self.log('test_R2_flipped_R2', self.R2score_flipped(y,logits))
        self.log('test_R2_normal_R2', self.R2score_normal(logits,y))
        self.log('test_rmse', self.MSE(logits, y))
        self.log('test_pearson_corr', self.pearson_cor(logits, y))
        
        return loss
    def predict_step(self, batch, batch_idx):
        x = batch
        pred = self(x)
        return pred

    def configure_optimizers(self):
        '''defines model optimizer'''
        return Adam(self.parameters(), lr=self.lr)

# Data Loader functions(train, valid, test)

# Define collate function


In [21]:
from torch.utils.data.sampler import WeightedRandomSampler
import torch

class ATACDataModule(pl.LightningDataModule):
    def __init__(self, one_hot_enc_genome, train_bed_file_df,valid_bed_file_df,test_bed_file_df,frag_tn5_train_df,frag_tn5_valid_df,frag_tn5_test_df, batch_size=128):
        super().__init__()
        self.one_hot_enc_genome = one_hot_enc_genome
        self.train_bed_file_df = train_bed_file_df
        self.valid_bed_file_df = valid_bed_file_df
        self.test_bed_file_df = test_bed_file_df
        self.frag_tn5_train_df = frag_tn5_train_df
        self.frag_tn5_valid_df = frag_tn5_valid_df
        self.frag_tn5_test_df = frag_tn5_test_df
        self.batch_size = batch_size
    # collate function for removing none from batch
    # def collate_fn(self, batch):
    #     batch = list(filter(lambda x: x is not None, batch))
    #     return torch.utils.data.dataloader.default_collate(batch)
    def setup(self, stage=None):
        '''called on each GPU separately - stage defines if we are at fit or test step'''
        # we set up only relevant datasets when stage is specified (automatically set by Pytorch-Lightning)
        if stage == 'fit' or stage is None:
            self.train_ds = Dataset_class(one_hot_enc_genome, train_bed_file_df, frag_tn5_train_df, dtype = torch.float32, bin_size = 512)
            self.valid_ds = Dataset_class(one_hot_enc_genome, valid_bed_file_df, frag_tn5_valid_df,dtype = torch.float32, bin_size = 512)
        if stage == 'test' or stage is None:
            self.test_ds = Dataset_class(one_hot_enc_genome, test_bed_file_df, frag_tn5_test_df,bin_size = 512)
            
    def train_dataloader(self):
        '''returns training dataloader'''
        sampler = WeightedRandomSampler(weights=torch.ones(len(self.train_ds)), num_samples=6400)
        train_dl = DataLoader(self.train_ds, sampler=sampler,batch_size=self.batch_size, num_workers=4)
        return train_dl

    def val_dataloader(self):
        '''returns validation dataloader'''
        valid_dl = DataLoader(self.valid_ds,shuffle=False, batch_size=self.batch_size,num_workers=4)
        return valid_dl

    def test_dataloader(self):
        '''returns test dataloader'''
        test_dl = DataLoader(self.test_ds,  shuffle=False,  batch_size=self.batch_size,num_workers=4)
        # collate_fn=self.collate_fn
        # , num_workers=4
        return test_dl

# WandB

In [ ]:
wandb.login()

In [ ]:
wandb_logger = WandbLogger()

# Training the model

In [38]:
import torch
import torchmetrics

# Setup  model
model = LitNN(seq_len=1024, channels= 4,num_classes=1, n_layer_1=128, n_layer_2=64, n_layer_3=32,lr=1e-1)


In [39]:
# Instantiate ATAC Data module
atac = ATACDataModule(one_hot_enc_genome, train_bed_file_df,valid_bed_file_df,test_bed_file_df,fikt_3,fikt_3,fikt_3, batch_size=64)

NameError: name 'train_bed_file_df' is not defined

In [ ]:
# from pytorch_lightning.callbacks.early_stopping import EarlyStopping
# # Early stopping 
# early_stop_callback = EarlyStopping(monitor="valid_loss", patience=10, mode="min")

In [ ]:
# Trainer initializer
trainer = pl.Trainer(
    # callbacks=[early_stop_callback],
    # auto_lr_find=True,
    gradient_clip_val=1,
    logger=wandb_logger,
    #overfit_batches= 0.1,
    # fast_dev_run = True,
    accelerator='auto', # W&B integration 
    #devices=1 if torch.cuda.is_available() else None,
    max_epochs=100 # number of epochs,
    )

In [ ]:
# Choose best LR automatically
trainer.tune(model,atac)

In [ ]:
lr_finder = trainer.tuner.lr_find(model, atac)

In [ ]:
fig = lr_finder.plot(suggest=True)
fig.show()

In [ ]:
# Define the LR with the best chosen LR
model.lr = 1e-7

In [ ]:
model.lr

In [ ]:
# Train the model
trainer.fit(model, atac)

In [ ]:
torch.__version__

In [ ]:
# Test model
trainer.test(model, atac)


In [ ]:
# clos wandb
wandb.finish()